In [325]:
%run -m ipy_startup
%run -m ipy_seaborn
%run -m ipy_plotly
from py_utils.notebook_utils import get_code_toggle
get_code_toggle(True)

# CAR-T Pipeline Results

This notebook will look at how well this pipeline recovers some known CAR-T target antigens.  In other words, if this pipeline was used to rank-order a list of CAR-T targets, would the following known targets be near the top of that list?

|Antigen|Full name|Disease|
|------|---------|------|
|EGFR|Epidermal growth factor receptor|NSCLC, epithelial carcinoma, glioma|
|EGFRvIII|Variant III of the epidermal growth factor receptor|Glioblastoma|
|HER2|Human epidermal growth factor receptor 2|Ovarian cancer, breast cancer, glioblastoma, colon cancer, osteosarcoma, medulloblastoma|
|MSLN|Mesothelin|Mesothelioma, ovarian cancer, pancreatic adenocarcinoma|
|PSMA|Prostate-specific membrane antigen|Prostate cancer|
|CEA|Carcinoembryonic antigen|Pancreatic adenocarcinoma, breast cancer, colorectal carcinoma|
|GD2|Disialoganglioside 2|Neuroblastoma, melanoma|
|IL13Rα2|Interleukin-13Ra2|Glioma|
|GPC3|Glypican-3|Hepatocellular carcinoma|
|CAIX|Carbonic anhydrase IX|Renal cell carcinoma (RCC)|
|L1-CAM|L1 cell adhesion molecule|Neuroblastoma, melanoma, ovarian adenocarcinoma|
|CA125|Cancer antigen 125 (also known as MUC16)|Epithelial ovarian cancers|
|CD133|Cluster of differentiation 133 (also known as prominin-1)|Glioblastoma, cholangiocarcinoma (CCA)|
|FAP|Fibroblast activation protein|Malignant pleural mesothelioma (MPM)|
|CTAG1B|Cancer/testis antigen 1B (also known as NY-ESO-1)|Melanoma and ovarian cancer|
|MUC1|Mucin 1|Seminal vesicle cancer|
|FR-α|Folate receptor-α|Ovarian cancer|
|PSCA|Prostate stem cell antigen|Prostate cancer|

<center>Known CAR-T Targets (Most entries from [Chimeric antigen receptor T cells: a novel therapy for solid tumors](https://jhoonline.biomedcentral.com/articles/10.1186/s13045-017-0444-9))</center>

In [161]:
def search_genes(d, substr):
    d = d.reset_index()
    mask = d['Gene'].str.contains(substr) | d['Meta:GeneSynonym'].fillna('').str.contains(substr)
    return d[mask][['Gene', 'Meta:GeneSynonym']].drop_duplicates()
#search_genes(d, 'HER2')

In [170]:
# Generate mapping between CAR-T antigens to genes, as well as relevant TCGA studies
cart_targets = {
    #'EGFR': 'NSCLC, epithelial carcinoma, glioma',
    'EGFR': {'cancers': 'NSCLC, epithelial carcinoma, glioma', 'studies': ['luad', 'lgg']},
    #'EGFRvIII': 'Glioblastoma', # This is from a variant of the EGFR gene so it's not really possible to use here
    
    #'HER2': 'Ovarian cancer, breast cancer, glioblastoma, colon cancer, osteosarcoma, medulloblastoma',
    'ERBB2': {
        'cancers': 'Ovarian cancer, breast cancer, glioblastoma, colon cancer, osteosarcoma, medulloblastoma',
        'studies': ['brca', 'coadread']
    },
    
    'MSLN': {
        'cancers': 'Mesothelioma, ovarian cancer, pancreatic adenocarcinoma',
        'studies': ['paad', 'ov']
    },
    
    #'PSMA': 'Prostate cancer',
    'FOLH1': {'cancers': 'Prostate cancer', 'studies': ['prad']},
    'PSCA': {'cancers': 'Prostate cancer', 'studies': ['prad']},
    
    #'CEA': 'Pancreatic adenocarcinoma, breast cancer, colorectal carcinoma',
    'CEACAM5': {
        'cancers': 'Pancreatic adenocarcinoma, breast cancer, colorectal carcinoma',
        'studies': ['paad', 'brca', 'coadread']
    },
    'CEACAM7': {
        'cancers': 'Pancreatic adenocarcinoma, breast cancer, colorectal carcinoma',
        'studies': ['paad', 'brca', 'coadread']
    },
    
    #'GD2': 'Neuroblastoma, melanoma', # Can't find this one
    
    #'IL13Rα2': 'Glioma',
    'IL13RA2': {'cancers': 'Glioma', 'studies': ['lgg']},
    
    #'GPC3': 'Hepatocellular carcinoma', # Not using liver cancer TCGA study yet
    
    #'CAIX': 'Renal cell carcinoma (RCC)',
    'CA9': {
        'cancers': 'Renal cell carcinoma (RCC)',
        'studies': ['kirc']
    },
    
    #'L1-CAM': 'Neuroblastoma, melanoma, ovarian adenocarcinoma',
    'L1CAM': {
        'cancers': 'Neuroblastoma, melanoma, ovarian adenocarcinoma',
        'studies': ['ov', 'skcm']
    },
    
    #'CA125': 'Epithelial ovarian cancers',
    #'MUC16': 'Epithelial ovarian cancers', # This one is tricky since it's so specific .. not sure how to match to TCGA
    
    #'CD133': 'Glioblastoma, cholangiocarcinoma (CCA)',
    'PROM1': {
        'cancers': 'Glioblastoma, cholangiocarcinoma (CCA)',
        'studies': ['gbm']
    },
    
    'FAP': {
        'cancers': 'Malignant pleural mesothelioma (MPM)',
        'studies': ['meso']
    },
    
    'CTAG1B': {
        'cancers': 'Melanoma and ovarian cancer',
        'studies': ['skcm', 'ov']
    },
    
    'MUC1': {
        'cancers': 'Seminal vesicle cancer',
        'studies': ['prad']
    },
    
    #'FR-α': 'Ovarian cancer'
    'FOLR1': {'cancers': 'Ovarian cancer', 'studies': ['ov']}
}

## Pipeline Result Data

This frame contains expression statistics and gene metadata for each TCGA study.  This includes only about 6.5k genes per study as was intended by using the Human Protein Atlas to only collect data for genes associated with antigens that are one or more of the following:

1. Expressed on cell membranes
2. FDA-approved drug targets
3. Cancer-related genes
4. CD markers

Result info:

In [139]:
d = pd.read_csv('/Users/eczech/projects/hammer/cache/pipeline/pipeline_result.csv')
d = d.set_index(['StudyId', 'Gene'])
def totuple(v):
    return tuple([i.strip() for i in v.replace('(', '').replace(')', '').replace("'", "").split(',')])
d['Meta:ProteinClasses'] = d['Meta:ProteinClasses'].apply(totuple)

idx_names = d.index.names
d = d.reset_index()
d['StudyId'] = d['StudyId'].str.replace('_tcga', '')
d = d.set_index(idx_names)

d['Stat:Icov'] = d['Stat:Mean'] / d['Stat:Std']

d.info()

<class 'pandas.core.frame.DataFrame'>
MultiIndex: 76785 entries, (brca, TSPAN6) to (meso, ATRIP)
Data columns (total 24 columns):
Meta:GeneSynonym          66665 non-null object
Meta:Ensembl              76785 non-null object
Meta:Chromosome           76785 non-null object
Meta:RnaTissueCategory    76785 non-null object
Meta:RnaTs                34516 non-null float64
Meta:RnaTsTpm             34516 non-null object
Meta:ProteinClasses       76785 non-null object
Stat:Count                76785 non-null float64
Stat:Mean                 76785 non-null float64
Stat:Std                  76785 non-null float64
Stat:Min                  76785 non-null float64
Stat:10%                  76785 non-null float64
Stat:20%                  76785 non-null float64
Stat:30%                  76785 non-null float64
Stat:40%                  76785 non-null float64
Stat:50%                  76785 non-null float64
Stat:60%                  76785 non-null float64
Stat:70%                  76785 non-null fl

## Number of Genes by TCGA Study

In [140]:
d.reset_index().groupby('StudyId')['Gene'].nunique()

StudyId
brca        6325
coadread    6251
gbm         6225
kirc        6332
laml        6263
lgg         6329
luad        6512
meso        6412
ov          6532
paad        6466
prad        6586
skcm        6552
Name: Gene, dtype: int64

In [326]:
# df = d.reset_index()[['Gene', 'Meta:ProteinClasses']].drop_duplicates()
# df['Meta:ProteinClasses'].apply(lambda v: pd.Series(v)).stack().value_counts()

In [327]:
# df['Meta:ProteinClasses'].apply(lambda v: pd.Series(v)).stack().unique()

In [191]:
# Compute per-study ranks and percentiles (by gene)
stat = 'Stat:Mean'
#stat = 'Stat:Icov'
#stat = 'Stat:70%'
def rank(g):
    r = g.sort_values(stat, ascending=False).assign(Rank=np.arange(1, len(g)+1), Total=len(g))
    r['Percentile'] = 100*(1 - (r['Rank'] / r['Total']))
    return r
d_rank = d.reset_index().groupby('StudyId', group_keys=False).apply(rank)

In [328]:
#d_rank.head()

In [329]:
def get_rank_stats(d):
    res = []
    d = d.set_index(['StudyId', 'Gene'])
    for gene in cart_targets:
        for study_id in cart_targets[gene]['studies']:
            if d.index.contains((study_id, gene)):
                d_gene = d.loc[(study_id, gene)]
                res.append({
                    'Gene': gene,
                    'StudyId': study_id,
                    'Rank': d_gene['Rank'],
                    'Percentile': d_gene['Percentile'],
                    'Total': d_gene['Total'],
                    'RnaTissueCategory': d_gene['Meta:RnaTissueCategory'],
                    'RnaTs': d_gene['Meta:RnaTs'],
                    'MembraneProtein': 'Predicted membrane proteins' in d_gene['Meta:ProteinClasses'],
                    'FdaApproved': 'FDA approved drug targets' in d_gene['Meta:ProteinClasses'],
                    'Value': d_gene[stat]
                })
            else:
                pass
                #print('Failed to find data for gene "{}" and study "{}"'.format(gene, study_id))
    return pd.DataFrame(res)

## Rankings of Known CAR-T Targets

This table shows how each of the known antigens (or rather the genes corresponding to those anitgens) would rank across the whole distribution of gene expression, for each study:

In [330]:
d_rank_stat = get_rank_stats(d_rank).set_index(['StudyId', 'Gene'])
d_rank_stat.sort_values('Percentile')

FdaApproved  MembraneProtein  Percentile  Rank  \
StudyId  Gene                                                      
kirc     CA9            False             True   12.539482  5538   
ov       MSLN           False             True   16.916718  5427   
         L1CAM          False             True   20.713411  5179   
prad     FOLH1           True             True   24.066201  5001   
paad     CEACAM7        False             True   37.875039  4017   
lgg      IL13RA2        False             True   40.780534  3748   
coadread CEACAM7        False             True   48.424252  3224   
brca     CEACAM5        False            False   49.739130  3179   
skcm     CTAG1B         False            False   52.777778  3094   
         L1CAM          False             True   52.991453  3080   
gbm      PROM1          False             True   55.919679  2744   
coadread CEACAM5        False            False   67.909135  2006   
ov       CTAG1B         False            False   76.576852  1530   
meso     FAP            False            False   76.606363  1500   
paad     MSLN           False             True   78.657594  1380   
ov       FOLR1          False             True   83.328230  1089   
prad     PSCA           False             True   85.408442   961   
brca     CEACAM7        False             True   86.924901   827   
prad     MUC1           False             True   95.687823   284   
coadread ERBB2           True             True   99.280115    45   
luad     EGFR            True             True   99.339681    43   
lgg      EGFR            True             True   99.826197    11   
brca     ERBB2           True             True   99.920949     5   

                 RnaTissueCategory  RnaTs  Total     Value  
StudyId  Gene                                               
kirc     CA9       Tissue enhanced    0.0   6332 -0.076037  
ov       MSLN       Group enriched    9.0   6532 -0.194422  
         L1CAM     Tissue enhanced    0.0   6532 -0.158554  
prad     FOLH1      Group enriched    6.0   6586 -0.028207  
paad     CEACAM7    Group enriched    7.0   6466 -0.041450  
lgg      IL13RA2   Tissue enriched    8.0   6329 -0.013965  
coadread CEACAM7    Group enriched    7.0   6251  0.002322  
brca     CEACAM5   Tissue enhanced    0.0   6325 -0.002487  
skcm     CTAG1B    Tissue enriched   46.0   6552 -0.000785  
         L1CAM     Tissue enhanced    0.0   6552 -0.000031  
gbm      PROM1     Tissue enhanced    0.0   6225  0.001654  
coadread CEACAM5   Tissue enhanced    0.0   6251  0.054623  
ov       CTAG1B    Tissue enriched   46.0   6532  0.136900  
meso     FAP       Tissue enhanced    0.0   6412  0.088064  
paad     MSLN       Group enriched    9.0   6466  0.070785  
ov       FOLR1     Tissue enhanced    0.0   6532  0.223567  
prad     PSCA      Tissue enhanced    0.0   6586  0.050231  
brca     CEACAM7    Group enriched    7.0   6325  0.207863  
prad     MUC1      Tissue enhanced    0.0   6586  0.136467  
coadread ERBB2    Expressed in all    NaN   6251  1.868154  
luad     EGFR      Tissue enhanced    0.0   6512  0.994623  
lgg      EGFR      Tissue enhanced    0.0   6329  1.105172  
brca     ERBB2    Expressed in all    NaN   6325  3.215520

## Plot Top Rankings

This plot shows the most over-expressed genes in each study and highlights those that are known CAR-T targets:

In [322]:
def plot_ranks(d):
    traces = []
    for k, g in d.groupby('StudyId'):
        g = g.head(100)
        sizes = g['Gene'].apply(lambda v: 15 if v in cart_targets and k in cart_targets[v]['studies'] else 4)
        def get_text(r):
            gene = r['Gene']
            if gene not in cart_targets:
                text = 'Gene: {}'.format(gene)
            else:
                text = 'Gene: {}<br>Cancers Under Evaluation for CAR-T Therpay:<br>{}'.format(gene, cart_targets[gene]['cancers'])
            return text
        text = g.apply(get_text, axis=1).values

        traces.append(go.Scatter(
            x=np.arange(1, len(g)+1),
            y=g[stat],
            name=k,
            text=text,
            mode='markers',
            marker=dict(size=sizes)
        ))
    layout = go.Layout(
        yaxis=go.YAxis(type='log', autorange=True, title='Mean RNA Z-Score'),
        xaxis=go.XAxis(title='Expression Rank in Study (of ~6500 genes)'),
        hovermode='closest',
        title='Top Expression Scores by TCGA Study<br><i>*Known CAR-T Genes drawn as larger circles</i>'
    )
    fig = go.Figure(data=traces, layout=layout)
    plty.offline.iplt(fig)
plot_ranks(d_rank)

## Plot Full Expression Distribution

Clearly many of the genes for target antigens aren't ending up near the top of the list of the most overexpressed genes, so this plot shows the full distribution of those expression scores and where each target antigen/gene falls:

In [324]:
#from plotly.figure_factory import create_distplot
np.random.seed(1)

def get_dist_parts(i, d, d_rank_stat, study_id, max_val=.5, min_val=.4):
    traces = [
        go.Histogram(
            x=d.loc[study_id][stat].clip(-min_val, max_val), 
            opacity=.5, showlegend=False, name=study_id,
            marker=dict(color='rgb(31, 119, 180)')
        ),
    ]
    
    annotations=[]
    for gene, r in d_rank_stat.loc[study_id].iterrows():
        if not r['MembraneProtein']:
            color = 'rgb(127, 127, 127)'
        elif r['RnaTissueCategory'] == 'Tissue enhanced':
            color = 'rgb(44, 160, 44)'
        else:
            color = 'rgb(255, 127, 14)'
        ax = str(i)
        text = 'Gene: {}<br>Mean RNA Z-Score: {:.6f}<br>Percentile: {:.2f}<br>'\
                'Typicaly On Cell Membrane: {}<br>Tissue Specificity Category: {}'.format(
                gene, r['Value'], r['Percentile'], r['MembraneProtein'], r['RnaTissueCategory'])
        annotation = dict(
            x=min(r['Value'], max_val),
            y=0,
            xref='x{}'.format(ax),
            yref='y{}'.format(ax),
            text=gene,
            font=dict(color=color),
            showarrow=True,
            hovertext=text,
            ax=0,
            ay=-np.random.randint(15, 60)
        )
        annotations.append(annotation)
        
    return traces, annotations
    
from plotly.tools import make_subplots

def dummy_scatter(color, name):
    return go.Scatter(x=[0], y=[np.nan], name=name, showlegend=True, marker=dict(color=color))

def plot_dists(d, d_rank_stat):
    study_ids = list(d_rank_stat.index.get_level_values('StudyId').unique())
    fig = make_subplots(
        rows=len(study_ids), cols=1, print_grid=False,
        subplot_titles=study_ids
    )
    
    annotations = []
    for i,study_id in enumerate(study_ids):
        traces, annots = get_dist_parts(i+1, d, d_rank_stat, study_id)
        annotations.extend(annots)
        for trace in traces:
            fig.append_trace(trace, i+1, 1)
    fig.append_trace(dummy_scatter('rgb(127, 127, 127)', 'Not on Cell Membrane'), 1, 1)            
    fig.append_trace(dummy_scatter('rgb(44, 160, 44)', 'On Cell Membrane, High Tissue Specificity'), 1, 1)
    fig.append_trace(dummy_scatter('rgb(255, 127, 14)', 'On Cell Membrane, Lower Tissue Specificity'), 1, 1)
    fig['layout']['xaxis{}'.format(len(study_ids))].update(title='Mean RNA Z-Score')
    fig['layout']['yaxis1'].update(title='# Genes')
    fig['layout']['annotations'].extend(annotations)
    fig['layout'].update(height=1600, title='Distribution of Mean RNA Z-Scores by TCGA Study')
    plty.offline.iplt(fig)
    return fig

fig = plot_dists(d, d_rank_stat)

# Conclusions

1. Using TCGA RNA-seq data and the Human Protein Atlas (HPA) to do nothing other than filter to genes expressed on cell membranes and that are highly over-expressed in cancers does not appear to be a great way to "reverse-engineer" the discovery methods used for current, known CAR-T target antigens.  Or at least, this method would still need to produce lists of targets thousands of proteins long before also including most of the known targets.
2. One great way to improve this pipeline would be to figure out what is about the genes that are overexpressed to a much greater extent than CAR-T targets that DID NOT make them good candidates.  Some possible explanations for that and good future additions would be:
    - Determine which genes/proteins are necessary for cell survival
    - Determine which genes/proteins are over-expressed in a stable, preditable way across cells for a SINGLE patient
3. Given that there are ~20k protein coding genes, simply using the HPA data to focus on only cell membrane proteins, those FDA-approved as drug targets, CD markers, or cancer-related gave a list of ~6.5k genes that was at least broad enough to capture ALL known CAR-T targets used here -- that's an encouraging sign since it at least means that the pipeline is in the right ballpark (and accurately reduced the scope of genes to assess by ~1/3).